## e621.net/e6ai.net JSON to `.txt` tags
----

This Python script is designed to process JSON files found within a specified directory and its subdirectories. Each JSON file is expected to contain data related to image posts, particularly sourced from online platforms such as image boards. The script parses these JSON files, extracts relevant information such as image URL, ratings, and tags, and generates caption files (`.txt`) based on this data.

Here's a breakdown of what the script does:

1. **Ignoring Tags**: The script defines a list of tags to be ignored during processing, such as "hi res", "shaded", etc.

2. **Processing Files**: The `process_file` function is responsible for processing each JSON file. It reads the JSON data, extracts the URL of the image file, determines its rating, and extracts tags associated with the image.

3. **Generating Caption File**: For each image, a caption file is generated with the same name as the image file but with a .txt extension. The rating of the image is written first, followed by processed tags.

4. **Processing Tags**: Tags are processed to replace underscores with spaces and to handle special cases such as artist tags. Ignored tags are filtered out.

In [1]:
# Define tags to be ignored using regular expressions for exact matching
ignored_tags = [r"\bblizzard entertainment\b", r"\bwarcraft\b",
    r"(?:\d{4})|(?:\d+:\d+)",
    r"\bdetailed\b", r"\bwidescreen\b", r"\b4k\b",
    r"\babsurd res\b", r"\bhi res\b", r"\bshaded\b",  r"\bdetailed\b",
    r"\btagme\b",
    r"\bdota\b",
    r"\bcreative commons\b", r"\bcc-by-nc-nd\b",
    r"\bsquare enix\b", r"\bfinal fantasy xiv\b", r"\bfinal fantasy\b",
    r"\bmythological canine\b", r"\basian mythology\b", r"\bmythological scalie\b",
    r"\bancient pokemon\b", r"\bmythological creature\b", r"\blegendary pokemon\b",
    r"\bfelis\b", r"\bfelid\b",
    r"\bsega\b",
    r"\bhasbro\b",
    r"\bzootopia\b",
    r"\bfive nights at freddy's\b",
    r"\beeveelution\b",
    r"\bdisney\b",
    r"\bmammal\b", r"\bcanis\b", r"\bcanine\b", r"\bcanid\b",
    r"\bdigimon\b", r"\bbandai namco\b",
    r"\bpokemon (species)\b",
    r"\bpal (species)\b",
    r"\bpokemon\b", r"\bnintendo\b",
    r"\\bby conditional dnp\\b",
    r"\\bconditional dnp\\b",
    r"\\bconditional_dnp\\b",
    r"\\bby\\s+conditional\\s+dnp\\b",
    r"\bgeneration\s+\d+\s+pokemon\b",
]

In [2]:
import os
import glob
import re
import json
from rich.console import Console
from rich.table import Table

console = Console()


# Function to check if a tag should be ignored based on the ignored_tags list
def should_ignore_tag(tag):
    for ignored_tag_pattern in ignored_tags:
        pattern = re.compile(ignored_tag_pattern, re.VERBOSE | re.IGNORECASE)
        if re.search(pattern, tag):
            return True
    return False


# Function to process tags and determine if they should be ignored
def process_tags(tags_dict):
    processed_tags = []
    for category, tags_list in tags_dict.items():
        category_tags = []
        if category == "artist":
            category_tags = [
                f"by {tag.replace('_', ' ').replace(' (artist)', '')}"
                for tag in tags_list
                if tag
            ]
        else:
            for tag in tags_list:
                tag = tag.replace("_", " ")
                # Escape unescaped parentheses
                tag = re.sub(r"(?<!\\)\(", r"\(", tag)
                tag = re.sub(r"(?<!\\)\)", r"\)", tag)
                if tag.lower() == "artist":
                    continue
                if not should_ignore_tag(tag):
                    category_tags.append(tag)
        processed_tags.extend(category_tags)
    return processed_tags


# Modify the process_file function to use the updated process_tags function
def process_file(file_path):
    try:
        console.print(f"Processing file: [bold]{file_path}[/bold]")
        with open(file_path, "r") as f:
            data = json.load(f)
        # Parse the URL and generate filename
        post_data = data.get("post", {})
        file_data = post_data.get("file", {})
        url = file_data.get("url")
        if url:
            filename, ext = os.path.splitext(os.path.basename(url))
            # Create caption file
            caption_file = f"{filename}.txt"
            caption_path = os.path.join(os.path.dirname(file_path), caption_file)
            with open(caption_path, "w", encoding="utf-8") as f:
                # Write rating
                rating = post_data.get("rating", "q")
                if rating == "s":
                    f.write("rating_safe, ")
                elif rating == "e":
                    f.write("rating_explicit, ")
                else:
                    f.write("rating_questionable, ")
                # Process tags
                tags_data = post_data.get("tags", {})
                processed_tags = process_tags(tags_data)
                # Check if there are any valid tags before writing
                if processed_tags:
                    # Join tags with commas and write to file
                    tags_line = ", ".join(processed_tags)
                    f.write(tags_line.strip())

                    # Create a table
                    table = Table(show_header=True, header_style="bold magenta")
                    table.add_column(caption_path, justify="center")

                    table.add_row(tags_line.strip())

                    # Print the table
                    console.print(table)
    except Exception as e:
        console.print(f"Error processing file: [bold]{file_path}[/bold]")
        console.print(e)


def recursive_process(directory):
    for file_path in glob.glob(directory + "/**/*.json", recursive=True):
        process_file(file_path)


if __name__ == "__main__":
    root_directory = r"E:\training_dir"
    # root_directory = r"C:\Users\kade\Desktop\training_dir_staging"
    recursive_process(root_directory)

Processing file: E:\training_dir\anal_beads_in_ass\1300374.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                     E:\training_dir\anal_beads_in_ass\28cee8b5602853039c8df57b4923d46c.txt                      ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ amber eyes, anal, anal beads, anal beads in ass, anal juice, anal penetration, animal genitalia, animal pussy,  │
│   anthro, anus, big breasts, big butt, big clitoris, big teats, biped, black anus, black border, black pussy,   │
│   bodily fluids, border, breasts, breasts and teats, butt, cervix, clitoral winking, clitoris, crotch teats,    │
│ curvy figure, enlarged clitoral glans, equine genitalia, equine pussy, female, gaping, gaping pussy, genitals,  │
│ hair, half-closed eyes, horn, huge butt, inverted nipples, lactating, long hair, long neck, looking at viewer,  │
│ milk, multi breast, narrowed eyes, nipples, nude, object in ass, orange eyes, penetration, pink clitoris, plump │
│    labia, presenting, presenting anus, presenting pussy, presenting teats, puffy anus, puffy nipples, pussy,    │
│   raised tail, rear view, sex toy, sex toy in ass, sex toy insertion, side boob, sitting, smile, solo, tail,    │
│  teats, thick thighs, urethra, voluptuous, wide hips, by r-mk, mythology, baat, dragon, mythological creature,  │
│                     mythological scalie, reptile, scalie, digital media \(artwork\), hi res                     │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\anal_beads_in_ass\1307329.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                     E:\training_dir\anal_beads_in_ass\c9144d05076eb7d1a1ac097654717d3e.txt                      ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│   anal, anal beads, anal beads in ass, anal penetration, anthro, bodily fluids, female, fur, genital fluids,    │
│ genitals, hair, humanoid genitalia, humanoid pussy, object in ass, open mouth, penetration, pokeball, pokeball  │
│ anal beads, pokeball insertion, pokeball sex toy, pokemorph, pussy, sex toy, sex toy in ass, sex toy insertion, │
│    solo, spread legs, spreading, standard pokeball, tongue, tongue out, vaginal fluids, by eto ya, glaceon,     │
│                                        digital media \(artwork\), hi res                                        │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\anal_beads_in_ass\1530325.json

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                            E:\training_dir\trio\2b1d1b630862c7f81f74f0d701801306.txt                            ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ anthro, black sclera, blank stare, blep, blush, blush lines, bodily fluids, claws, collaborative, collaborative │
│    fellatio, collaborative sex, cum, cum on snout, cum on tongue, dialogue, dripping, drooling, drooling on     │
│   partner, feathers, fellatio, female, fur, genital fluids, genitals, googly eyes, group, heart symbol, human   │
│     penetrating, humor, interspecies, larger female, licking, male, male/female, oral, oversized fellatio,      │
│  oversized oral, palphilia, penetration, penile, penis, penis lick, pokephilia, saliva, saliva drip, saliva on  │
│    penis, saliva on tongue, sex, silly, silly face, simple background, size difference, sweat, text, tongue,    │
│    tongue out, trio, upset, by storm, european mythology, mythology, palworld, pocketpair, dragon, feathered    │
│  dragon, furred dragon, human, mythological creature, mythological scalie, pal \(species\), quivern, reshiram,  │
│    scalie, western dragon, winged dragon, crossover, digital media \(artwork\), english text, lol comments,     │
│                                               sketch, spot color                                                │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\trio\4633026.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                            E:\training_dir\trio\2f760568ab38ab1af253181179cf1896.txt                            ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│    4 toes, accessory, anal, anal fingering, anthro, anthro on anthro, anthro penetrated, anthro penetrating,    │
│    anthro penetrating anthro, anus, balls, big penis, blonde hair, bodily fluids, bow ribbon, breasts, butt,    │
│  cervical penetration, claws, clothing, cum, cum from nose, cum from pussy, cum in mouth, cum in nose, cum in   │
│  pussy, cum in uterus, cum inside, cum on feet, cum string, cumshot, disembodied penis, ejaculation, erection,  │
│ feet, female, female penetrated, fingering, foreskin, fucked silly, fur, furgonomics, genital fluids, genitals, │
│   group, group sex, hair, hand on hair, humanoid genitalia, humanoid penis, impregnation, internal, legwear,    │
│ male, male/female, male penetrating, male penetrating female, orgasm, ovum, pawpads, penetration, penis, pussy, │
│ ribbons, roast, saliva, sex, soles, sperm cell, stirrup stockings, stockings, tail, tail accessory, tail anus,  │
│  tail bow, tail ribbon, thigh highs, threesome, thumb in ass, toe claws, toes, trio, uterus, vaginal, vaginal   │
│     penetration, white body, white fur, by tofu froth, final fantasy, final fantasy ix, square enix, freya      │
│                             crescent, burmecian, murid, murine, rat, rodent, hi res                             │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\trio\587729.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                            E:\training_dir\trio\dddf4a9b7f5ca93b1cefe007f08d2181.txt                            ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│   3 fingers, abdominal bulge, ahegao, all fours, ambiguous penetration, annoyed, balls deep, bestiality, big    │
│ breasts, bisexual, bisexual train, blue eyes, blush, bodily fluids, breasts, butt, clothing, cum, cum drip, cum │
│   in ass, cum in mouth, cum in pussy, cum inflation, cum inside, cum on butt, cum on leg, cum on tongue, cum    │
│ splatter, cum string, cum while penetrated, dialogue, doggystyle, dripping, drooling, excessive cum, excessive  │
│   genital fluids, eye roll, eyebrows, feet, female, female/female, female on feral, feral, feral penetrating,   │
│   feral penetrating human, fingerless gloves, fingers, footwear, forced, from behind position, fucked silly,    │
│   genital fluids, glistening, glistening body, gloves, green body, group, group sex, hair, handwear, human on   │
│  feral, human penetrated, inflation, interspecies, leaking cum, legwear, looking pleasured, male, male/female,  │
│    male penetrating, multicolored body, nipples, nude, open mouth, orgasm, penetration, pokeball, pokemorph,    │
│ pokephilia, purple body, raised inner eyebrows, rape, red hair, saliva, saliva string, sex, simple background,  │
│   simultaneous orgasms, slime, socks, standard pokeball, tail, talking feral, text, threesome, tongue, tongue   │
│  out, train position, trainer, trio, two tone body, white background, white body, by slugbox, by stickysheep,   │
│      mythology, scout \(stickysheep\), dragon, gardevoir, goodra, human, humanoid, mythological creature,       │
│                            mythological scalie, scalie, collaboration, english text                             │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

## Delete every JSON file ⚠️

---

In [4]:
import glob
import os

def delete_json_files(directory):
    # Create the path pattern to match JSON files
    pattern = os.path.join(directory, '**', '*.json')
    
    # Find all JSON files using glob
    json_files = glob.glob(pattern, recursive=True)
    
    # Delete each JSON file
    for file_path in json_files:
        try:
            os.remove(file_path)
            print(f"Deleted: {file_path}")
        except OSError as e:
            print(f"Error deleting {file_path}: {e}")

if __name__ == "__main__":
    # Specify the directory path
    directory_path = r'E:\training_dir'
    
    # Call the function to delete JSON files recursively
    delete_json_files(directory_path)

Deleted: E:\training_dir\anal_beads_in_ass\1300374.json
Deleted: E:\training_dir\anal_beads_in_ass\1307329.json
Deleted: E:\training_dir\anal_beads_in_ass\1530325.json
Deleted: E:\training_dir\anal_beads_in_ass\1574752.json
Deleted: E:\training_dir\anal_beads_in_ass\2136120.json
Deleted: E:\training_dir\anal_beads_in_ass\2279713.json
Deleted: E:\training_dir\anal_beads_in_ass\2285900.json
Deleted: E:\training_dir\anal_beads_in_ass\2347655.json
Deleted: E:\training_dir\anal_beads_in_ass\2366462.json
Deleted: E:\training_dir\anal_beads_in_ass\2405966.json
Deleted: E:\training_dir\anal_beads_in_ass\2422217.json
Deleted: E:\training_dir\anal_beads_in_ass\2443381.json
Deleted: E:\training_dir\anal_beads_in_ass\2459570.json
Deleted: E:\training_dir\anal_beads_in_ass\2491731.json
Deleted: E:\training_dir\anal_beads_in_ass\2531922.json
Deleted: E:\training_dir\anal_beads_in_ass\2538765.json
Deleted: E:\training_dir\anal_beads_in_ass\2586069.json
Deleted: E:\training_dir\anal_beads_in_ass\26368